In [0]:
# Caminhos
silver_path = "/mnt/eoliveira/silver/museusbr"
bronze_path = "/mnt/eoliveira/bronze/museusbr"

# Leitura da Bronze
df_bronze = spark.read.parquet(bronze_path)

# ✅ Resumo da Camada Silver 


| Módulo | Função                                                                                                                                                                    |
| ------ | ------------------------------------------------------------------------------------------------------------------------------------------------------------------------- |
| 1      | **Preparação da Coluna de Localização**: limpeza com `trim`, verificação com `isNotNull` e `contains` e split seguro em `Latitude` e `Longitude` usando `when/otherwise`. |
| 2      | **Seleção de Colunas**: escolha e renomeação de colunas principais com `select` e `alias`, incluindo `Latitude` e `Longitude` gerados no módulo anterior.                 |
| 3      | **Criação da UDF `mapear_regiao`**: definição da função que classifica a `UF` em sua respectiva Região brasileira e registro como UDF no Spark.                           |
| 4      | **Limpeza e Normalização**: aplicação de `coalesce` para tratamento de nulos, além de `trim`, `initcap` e `upper` para padronização dos textos.                           |
| 5      | **Validação de Campos Nulos**: definição da função `validar_campos_nulos` utilizando `reduce` e `filter` para identificar registros com campos críticos faltando.         |
| 6      | **Salvamento da Silver**: gravação final do DataFrame limpo (`df_silver_clean`) no Data Lake em formato Parquet com `overwrite` e mensagem de sucesso.                    |


### Seleção e transformação dos campos para Silver

In [0]:
from pyspark.sql.functions import col, trim, upper, initcap, coalesce, lit, udf, split, when, length, lower, concat_ws, regexp_replace, regexp_extract
from pyspark.sql.types import StringType

In [0]:
# Preparar a coluna limpa de localização
location_col = trim(col('metadata.location.value_as_string'))
tem_coordenadas = (location_col.isNotNull()) & (length(location_col) > 0) & (location_col.contains(","))

latitude_col = when(tem_coordenadas, split(location_col, ',').getItem(0).cast('double')).otherwise(lit(0.0))
longitude_col = when(tem_coordenadas, split(location_col, ',').getItem(1).cast('double')).otherwise(lit(0.0))

In [0]:

# Seleção das colunas principais
df_silver = df_bronze.select(
    col('id').cast('long').alias('Id'),
    col('title').alias('Instituicoes'),
    col('slug').alias('Slug'),
    concat_ws(", ", col('metadata.telefone.value')).alias('Telefone'),
    concat_ws(", ", col('metadata.email.value')).alias('Email'),
    concat_ws(", ", col('metadata.site-4.value')).alias('Site'),
    col('metadata.uf.value_as_string').alias('UF'),
    col('metadata.municipio.value_as_string').alias('Cidade'),
    col('metadata.logradouro.value_as_string').alias('Endereco'),
    col('description').alias('Descricao'),
    col('metadata.mus_tipo.value_as_string').alias('Tipo'),
    col('metadata.mus_tipo_tematica.value_as_string').alias('Tematica'),
    col('metadata.dias-e-horarios-de-abertura-para-o-publico.value').alias('Dias-Horarios-Abertura'),
    concat_ws(", ", col('metadata.valor-da-entrada.value')).alias('Valor-Entrada'),
    col('metadata.a-entrada-ao-museu-e-cobrada.value').alias('Entrada-Cobrada'),
    col('metadata.o-museu-promove-visitas-com-guia-mediador-monitor-educador-orientador.value').alias('Visita-Guiada'),
    concat_ws(", ", col('metadata.cnpj.value')).alias('CNPJ'),
    concat_ws(", ", col('metadata.instituicao-mantenedora.value')).alias('Instituicao-Mantenedora'),
    latitude_col.alias('Latitude'),
    longitude_col.alias('Longitude')
)


In [0]:

# UDF para mapear região
def mapear_regiao(uf):
    regiao_norte = ['AC', 'AP', 'AM', 'PA', 'RO', 'RR', 'TO']
    regiao_nordeste = ['AL', 'BA', 'CE', 'MA', 'PB', 'PE', 'PI', 'RN', 'SE']
    regiao_centro_oeste = ['DF', 'GO', 'MT', 'MS']
    regiao_sudeste = ['ES', 'MG', 'RJ', 'SP']
    regiao_sul = ['PR', 'RS', 'SC']
    if uf in regiao_norte:
        return 'Norte'
    elif uf in regiao_nordeste:
        return 'Nordeste'
    elif uf in regiao_centro_oeste:
        return 'Centro-Oeste'
    elif uf in regiao_sudeste:
        return 'Sudeste'
    elif uf in regiao_sul:
        return 'Sul'
    else:
        return 'Desconhecida'

mapear_regiao_udf = udf(mapear_regiao, StringType())

In [0]:
# Limpeza e normalização

df_silver_clean = (
    df_silver
    .withColumn('Instituicoes', initcap(trim(col('Instituicoes'))))
    .withColumn('UF', upper(trim(col('UF'))))
    .withColumn('Cidade', initcap(trim(col('Cidade'))))
    .withColumn('Endereco', initcap(trim(col('Endereco'))))
    .withColumn('Descricao', trim(col('Descricao')))
    .withColumn('Tipo', regexp_replace(initcap(trim(col('Tipo'))), r'([a-z])([A-Z])', r'\1 \2'))
    .withColumn('Tematica', initcap(trim(col('Tematica'))))
    .withColumn('Regiao', mapear_regiao_udf(col('UF')))
    .withColumn('Slug', initcap(trim(col('Slug'))))
    .withColumn('Email', lower(trim(col('Email'))))
    .withColumn('Instituicao-Mantenedora', initcap(lower(trim(col('Instituicao-Mantenedora')))))
)


In [0]:

# Separar Aberto e Horario
df_silver_clean = df_silver_clean.withColumn(
    'Aberto',
    when(
        col('Dias-Horarios-Abertura').isNotNull() & (trim(col('Dias-Horarios-Abertura')) != ''),
        trim(regexp_replace(split(col('Dias-Horarios-Abertura'), ':').getItem(0), r'\d+', ''))
    ).otherwise(lit('Não definido'))
).withColumn(
    'Horario',
    when(
        col('Dias-Horarios-Abertura').isNotNull() & (trim(col('Dias-Horarios-Abertura')) != ''),
        regexp_extract(col('Dias-Horarios-Abertura'), r'(\d{1,2}[:h]?\d{0,2})', 1)
    ).otherwise(lit('Não definido'))
).drop('Dias-Horarios-Abertura')


In [0]:
# Transformar Entrada-Cobrada e Visita-Guiada
df_silver_clean = df_silver_clean.withColumn(
    'Entrada-Cobrada',
    when(lower(trim(col('Entrada-Cobrada'))) == 'sim', lit('Sim')).otherwise(lit('Não'))
).withColumn(
    'Visita-Guiada',
    when(lower(trim(col('Visita-Guiada'))) == 'sim', lit('Sim')).otherwise(lit('Não'))
)

In [0]:
# Limpeza de caracteres especiais
for campo in ['Instituicoes', 'Endereco', 'Descricao', 'Tipo', 'Tematica', 'Cidade', 'Slug', 'Aberto']:
    df_silver_clean = df_silver_clean.withColumn(
        campo,
        regexp_replace(col(campo), '[^a-zA-Z0-9çÇáàãéèêíìóòõúùüÁÀÃÉÈÊÍÌÓÒÕÚÙÜ -]', '')
    )

In [0]:
# Lista de todas as colunas a tratar
colunas_a_tratar = [
    'Instituicoes', 'Slug', 'Telefone', 'Email', 'Site', 'UF', 'Cidade',
    'Endereco', 'Descricao', 'Tipo', 'Tematica', 'Valor-Entrada',
    'Entrada-Cobrada', 'Visita-Guiada', 'CNPJ', 'Instituicao-Mantenedora',
    'Aberto', 'Horario', 'Regiao'
]

In [0]:
# Aplicar tratamento para cada coluna: se null ou vazia → "Não informado"
for campo in colunas_a_tratar:
    df_silver_clean = df_silver_clean.withColumn(
        campo,
        when(col(campo).isNull() | (trim(col(campo)) == ''), lit('Não informado')).otherwise(trim(col(campo)))
    )

In [0]:
# Validação de nulos
def validar_campos_nulos(df, campos):
    from functools import reduce
    condicoes = [col(c).isNull() | (trim(col(c)) == '') for c in campos]
    return df.filter(reduce(lambda a, b: a | b, condicoes))

df_invalidos = validar_campos_nulos(df_silver_clean, colunas_a_tratar)
print("Registros inválidos encontrados:", df_invalidos.count())


Registros inválidos encontrados: 0


In [0]:
# Salvar camada Silver
silver_path = "/mnt/eoliveira/silver/museusbr"
df_silver_clean.write.mode("overwrite").parquet(silver_path)
print(f"✔ Silver salva com sucesso em: {silver_path}")

✔ Silver salva com sucesso em: /mnt/eoliveira/silver/museusbr


In [0]:
df_silver_clean.printSchema()

root
 |-- Id: long (nullable = true)
 |-- Instituicoes: string (nullable = true)
 |-- Slug: string (nullable = true)
 |-- Telefone: string (nullable = false)
 |-- Email: string (nullable = false)
 |-- Site: string (nullable = false)
 |-- UF: string (nullable = true)
 |-- Cidade: string (nullable = true)
 |-- Endereco: string (nullable = true)
 |-- Descricao: string (nullable = true)
 |-- Tipo: string (nullable = true)
 |-- Tematica: string (nullable = true)
 |-- Valor-Entrada: string (nullable = false)
 |-- Entrada-Cobrada: string (nullable = false)
 |-- Visita-Guiada: string (nullable = false)
 |-- CNPJ: string (nullable = false)
 |-- Instituicao-Mantenedora: string (nullable = false)
 |-- Latitude: double (nullable = true)
 |-- Longitude: double (nullable = true)
 |-- Regiao: string (nullable = true)
 |-- Aberto: string (nullable = true)
 |-- Horario: string (nullable = true)



In [0]:
# Visualização
display(df_silver_clean)

Id Instituicoes Slug Telefone Email Site UF Cidade Endereco Descricao Tipo Tematica Valor-Entrada Entrada-Cobrada Visita-Guiada CNPJ Instituicao-Mantenedora Latitude Longitude Regiao Aberto Horario 279033 Museu Tião Carreiro Museu-tiao-carreiro (14) 981380077 museu@institutojatobas.org.br https://www.institutojatobas.org.br/museu-tiao-carreiro SP Pardinho Praça Ademir Rocha Da Silva O Museu Tião Carreiro é um espaço dedicado à preservação da memória e do legado de um dos maioresnomes da música caipira Localizado no Centro Max Feffer em Pardinho SP e gerido pelo Instituto Jatobáso museu abriga um rico acervo de objetos fotos e registros que contam a trajetória de Tião Carreiro desdesuas origens até sua consagração como o Rei do Pagode Clássicotradicional Artes Arquitetura E Linguística Não informado Não Não 07.362.917/0002-66 Prefeitura Municipal De Pardinho E Instituto Jatobás -23.078688 -48.380063 Sudeste De Terça a Domingo das h às h 10h 277020 Museu Tabajara Povos Originários Da Serra Da Ibiapaba Museu-tabajara-povos-originarios-da-serra-da-ibiapaba (88) 992235195 fcaoneide@gmail.com https://www.instagram.com/associacaotabajaratianguaceara/ CE Tianguá Rua Capitão Odilon Aguiar O Museu Tabajara mencionado no estatuto da Associação dos Povos Indígenas da Serra da Ibiapaba refere-se ao Memorial ou Museu Indígena da Serra da Ibiapaba uma das principais iniciativas da associação para preservar e promover a cultura indígena local Suas finalidades incluemResgatar a memória e perpetuar os legados ancestrais dos povos indígenas da região como os Tabajara Tupinambá Tapuias e TremembésPromover a educação cultural por meio de exposições atividades escolares e visitas guiadas destacando a história tradições e contribuições dessas etniasConstruir uma Taba indígena como espaço de visitação simbolizando a arquitetura tradicional e servindo como ponto de conexão com a identidade indígenaIncentivar projetos de captação de recursos para sustentar ações culturais e educacionais além de lutar pela demarcação de terras indígenas na região Clássicotradicional História Não informado Não Não 53.039.805/0001-05 Associação Dos Povos Indígenas Da Serra Da Ibiapaba 0.0 0.0 Nordeste Sexta a Domingo de 07:30 273590 Casa Da Memória Roberto Antonio Marin Casa-da-memoria-roberto-antonio-marin (45) 32648602 acervocmm@medianeira.pr.gov.br https://casadamemoriademedianeira.com.br PR Medianeira Rua Argentina Somos uma Casa da Memória que recebe exposições itinerantes sobre variados temas Além disso temos como responsabilidade promover a pesquisa reconhecimento documentação preservação e divulgação da História de Medianeira como um espaço democrático de valorização das memórias da diversidade cultural do patrimnio histórico material e imaterial contribuindo para a construção da identidade do município Buscamos ser um espaço plural de referência histórico-cultural e guardião das memórias de Medianeira para que as futuras gerações possam conhecer e valorizar o passado a qual pertencem Clássicotradicional História Não informado Não Não Não informado Prefeitura Municipal De Medianeira -25.30182069025521 -54.10491943359376 Sul Segunda a sexta-feira das h - h 8h 270239 Memorial Da Democracia De Pernambuco Fernando De Vasconcellos Coelho Memorial-da-democracia-de-pernambuco-fernando-de-vasconcellos-coelho (81) 984941739 memorialdademocraciafvc@sjdh.pe.gov.br https://www.instagram.com/memorialdademocraciape/ PE Recife Estrada Do Arraial O Memorial da Democracia de Pernambuco Fernando de Vasconcellos Coelho vinculado à Secretaria de Justiça e Direitos Humanos se destina à guarda pesquisa e exposição de materiais e documentos que se refiram ou se vinculem ao esforço pela defesa e preservação da democracia da cidadania e dos direitos humanos no Estado de Pernambuco Clássicotradicional História Não informado Não Não Não informado Secretaria De Justiça E Direitos Humanos E Prevenção À Violência De Pernambuco -8.028533874148378 -34.911733909678105 Nordeste Ter a Sex h às hSáb

In [0]:
from pyspark.sql.functions import col, trim, upper, initcap, coalesce, lit, udf, split, when, length, lower, concat_ws, regexp_replace, regexp_extract
from pyspark.sql.types import StringType

# Preparar a coluna limpa de localização
location_col = trim(col('metadata.location.value_as_string'))
tem_coordenadas = (location_col.isNotNull()) & (length(location_col) > 0) & (location_col.contains(","))

latitude_col = when(tem_coordenadas, split(location_col, ',').getItem(0).cast('double')).otherwise(lit(0.0))
longitude_col = when(tem_coordenadas, split(location_col, ',').getItem(1).cast('double')).otherwise(lit(0.0))

# Seleção das colunas principais
df_silver = df_bronze.select(
    col('id').cast('long').alias('Id'),
    col('title').alias('Instituicoes'),
    col('slug').alias('Slug'),
    concat_ws(", ", col('metadata.telefone.value')).alias('Telefone'),
    concat_ws(", ", col('metadata.email.value')).alias('Email'),
    concat_ws(", ", col('metadata.site-4.value')).alias('Site'),
    col('metadata.uf.value_as_string').alias('UF'),
    col('metadata.municipio.value_as_string').alias('Cidade'),
    col('metadata.logradouro.value_as_string').alias('Endereco'),
    col('description').alias('Descricao'),
    col('metadata.mus_tipo.value_as_string').alias('Tipo'),
    col('metadata.mus_tipo_tematica.value_as_string').alias('Tematica'),
    col('metadata.dias-e-horarios-de-abertura-para-o-publico.value').alias('Dias-Horarios-Abertura'),
    concat_ws(", ", col('metadata.valor-da-entrada.value')).alias('Valor-Entrada'),
    col('metadata.a-entrada-ao-museu-e-cobrada.value').alias('Entrada-Cobrada'),
    col('metadata.o-museu-promove-visitas-com-guia-mediador-monitor-educador-orientador.value').alias('Visita-Guiada'),
    concat_ws(", ", col('metadata.cnpj.value')).alias('CNPJ'),
    concat_ws(", ", col('metadata.instituicao-mantenedora.value')).alias('Instituicao-Mantenedora'),
    latitude_col.alias('Latitude'),
    longitude_col.alias('Longitude')
)

# UDF para mapear região
def mapear_regiao(uf):
    regiao_norte = ['AC', 'AP', 'AM', 'PA', 'RO', 'RR', 'TO']
    regiao_nordeste = ['AL', 'BA', 'CE', 'MA', 'PB', 'PE', 'PI', 'RN', 'SE']
    regiao_centro_oeste = ['DF', 'GO', 'MT', 'MS']
    regiao_sudeste = ['ES', 'MG', 'RJ', 'SP']
    regiao_sul = ['PR', 'RS', 'SC']
    if uf in regiao_norte:
        return 'Norte'
    elif uf in regiao_nordeste:
        return 'Nordeste'
    elif uf in regiao_centro_oeste:
        return 'Centro-Oeste'
    elif uf in regiao_sudeste:
        return 'Sudeste'
    elif uf in regiao_sul:
        return 'Sul'
    else:
        return 'Desconhecida'

mapear_regiao_udf = udf(mapear_regiao, StringType())

# Limpeza e normalização
df_silver_clean = (
    df_silver
    .withColumn('Instituicoes', initcap(trim(col('Instituicoes'))))
    .withColumn('UF', upper(trim(col('UF'))))
    .withColumn('Cidade', initcap(trim(col('Cidade'))))
    .withColumn('Endereco', initcap(trim(col('Endereco'))))
    .withColumn('Descricao', trim(col('Descricao')))
    .withColumn('Tipo', regexp_replace(initcap(trim(col('Tipo'))), r'([a-z])([A-Z])', r'\1 \2'))
    .withColumn('Tematica', initcap(trim(col('Tematica'))))
    .withColumn('Regiao', mapear_regiao_udf(col('UF')))
    .withColumn('Slug', initcap(trim(col('Slug'))))
    .withColumn('Email', lower(trim(col('Email'))))
    .withColumn('Instituicao-Mantenedora', initcap(lower(trim(col('Instituicao-Mantenedora')))))
)

# Separar Aberto e Horario
df_silver_clean = df_silver_clean.withColumn(
    'Aberto',
    when(
        col('Dias-Horarios-Abertura').isNotNull() & (trim(col('Dias-Horarios-Abertura')) != ''),
        trim(regexp_replace(split(col('Dias-Horarios-Abertura'), ':').getItem(0), r'\d+', ''))
    ).otherwise(lit('Não definido'))
).withColumn(
    'Horario',
    when(
        col('Dias-Horarios-Abertura').isNotNull() & (trim(col('Dias-Horarios-Abertura')) != ''),
        regexp_extract(col('Dias-Horarios-Abertura'), r'(\d{1,2}[:h]?\d{0,2})', 1)
    ).otherwise(lit('Não definido'))
).drop('Dias-Horarios-Abertura')

# Transformar Entrada-Cobrada e Visita-Guiada
df_silver_clean = df_silver_clean.withColumn(
    'Entrada-Cobrada',
    when(lower(trim(col('Entrada-Cobrada'))) == 'sim', lit('Sim')).otherwise(lit('Não'))
).withColumn(
    'Visita-Guiada',
    when(lower(trim(col('Visita-Guiada'))) == 'sim', lit('Sim')).otherwise(lit('Não'))
)

# Limpeza de caracteres especiais
for campo in ['Instituicoes', 'Endereco', 'Descricao', 'Tipo', 'Tematica', 'Cidade', 'Slug', 'Aberto']:
    df_silver_clean = df_silver_clean.withColumn(
        campo,
        regexp_replace(col(campo), '[^a-zA-Z0-9çÇáàãéèêíìóòõúùüÁÀÃÉÈÊÍÌÓÒÕÚÙÜ -]', '')
    )

# Lista de todas as colunas a tratar
colunas_a_tratar = [
    'Instituicoes', 'Slug', 'Telefone', 'Email', 'Site', 'UF', 'Cidade',
    'Endereco', 'Descricao', 'Tipo', 'Tematica', 'Valor-Entrada',
    'Entrada-Cobrada', 'Visita-Guiada', 'CNPJ', 'Instituicao-Mantenedora',
    'Aberto', 'Horario', 'Regiao'
]

# Aplicar tratamento para cada coluna: se null ou vazia → "Não informado"
for campo in colunas_a_tratar:
    df_silver_clean = df_silver_clean.withColumn(
        campo,
        when(col(campo).isNull() | (trim(col(campo)) == ''), lit('Não informado')).otherwise(trim(col(campo)))
    )

# Validação de nulos
def validar_campos_nulos(df, campos):
    from functools import reduce
    condicoes = [col(c).isNull() | (trim(col(c)) == '') for c in campos]
    return df.filter(reduce(lambda a, b: a | b, condicoes))

df_invalidos = validar_campos_nulos(df_silver_clean, colunas_a_tratar)
print("Registros inválidos encontrados:", df_invalidos.count())

# Salvar camada Silver
silver_path = "/mnt/eoliveira/silver/museusbr"
df_silver_clean.write.mode("overwrite").parquet(silver_path)
print(f"✔ Silver salva com sucesso em: {silver_path}")


Registros inválidos encontrados: 0
✔ Silver salva com sucesso em: /mnt/eoliveira/silver/museusbr


In [0]:
from azure.identity import DefaultAzureCredential
from azure.keyvault.secrets import SecretClient
 
# Key Vault
vault_url = "https:/.vault.azure.net/"
credential = DefaultCredential()
client = SecretClient(vault_url=vault_url, credential=credential)
 
# Busca segredos
server_name = client.get_secret("r").value
database_name = client.get_secret("d").value
client_id = "cd4203c1-a9f1f"
client_secret = "bkx8Q~np~InBCcD1"
tenant_id = "3638027-c9d6d1e8"

 
# ✅ AQUI está o segredo: incluir clientId como user e clientSecret como password
jdbc_url = (
    f"jdbc:sqlserver://{server_name}:1433;"
    f"database={database_name};"
    f"user={client_id};"
    f"password={client_secret};"
    f"encrypt=true;"
    f"trustServerCertificate=false;"
    f"hostNameInCertificate=*.windows.net;"
    f"loginTimeout=30;"
    f"authentication=ActivecePrincipal;"
    f"authority=https://login.com/{tenant_id};"
)

# ✅ Agora funciona corretamente
df_silver_clean.write\
    .format("jdbc") \
    .option("url", jdbc_url) \
    .option("dbtable", "Elenir_Oliveira") \
    .option("driver", "com.microsoft..jdbc.Driver") \
    .mode("overwrite") \
    .save()
 
print("✅ Dados enviados com sucesso usando App Registration (Service Principal)!")


✅ Dados enviados com sucesso usando App Registration (Service Principal)!
